<a href="https://colab.research.google.com/github/mjgpinheiro/Physics_models/blob/main/learning_stability_prism_edges.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# Learning Stability — Prism with Vertical Edges

This notebook shows **a full prism** (top face, bottom face, and vertical edges)
twisting and relaxing inside a torus.

Now the geometry is unambiguous: **a body learning stability**.


In [2]:
import numpy as np
import plotly.graph_objects as go

# ---------------- Parameters ----------------
phi = (1 + 5**0.5)/2
tau = 30
frames_n = 80

R, r = 3.0, 0.8
prism_sides = 6
height = 1.4

theta = np.linspace(0, 2*np.pi, prism_sides, endpoint=False)

# ---------------- Torus mesh ----------------
u = np.linspace(0, 2*np.pi, 50)
v = np.linspace(0, 2*np.pi, 30)
U, V = np.meshgrid(u, v)
X = (R + r*np.cos(V)) * np.cos(U)
Y = (R + r*np.cos(V)) * np.sin(U)
Z = r * np.sin(V)

# ---------------- Prism dynamics ----------------
def prism_vertices(n):
    damp = np.exp(-n/tau)
    twist = 1.2 * damp * np.sin(theta + 0.15*n)
    x = 0.9 * np.cos(theta + twist)
    y = 0.9 * np.sin(theta + twist)
    z_top =  height/2
    z_bot = -height/2
    return x, y, z_top, z_bot

# ---------------- Initial frame ----------------
x, y, zt, zb = prism_vertices(0)

top = go.Scatter3d(
    x=x, y=y, z=[zt]*len(x),
    mode='lines+markers',
    line=dict(width=4),
    marker=dict(size=4),
    name="Top face"
)

bottom = go.Scatter3d(
    x=x, y=y, z=[zb]*len(x),
    mode='lines+markers',
    line=dict(width=4),
    marker=dict(size=4),
    name="Bottom face"
)

edges = []
for i in range(prism_sides):
    edges.append(go.Scatter3d(
        x=[x[i], x[i]],
        y=[y[i], y[i]],
        z=[zb, zt],
        mode='lines',
        line=dict(width=3),
        showlegend=False
    ))

fig = go.Figure(
    data=[
        go.Surface(x=X, y=Y, z=Z, opacity=0.25,
                   colorscale='Greys', showscale=False),
        top, bottom, *edges
    ],
    layout=go.Layout(
        title="Learning Stability: a Prism inside a Torus",
        scene=dict(
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
            aspectmode='data'
        ),
        updatemenus=[dict(
            type='buttons',
            showactive=False,
            buttons=[dict(label='Play',
                          method='animate',
                          args=[None])]
        )]
    )
)

# ---------------- Frames ----------------
frames = []
for n in range(frames_n):
    x, y, zt, zb = prism_vertices(n)

    frame_edges = []
    for i in range(prism_sides):
        frame_edges.append(go.Scatter3d(
            x=[x[i], x[i]],
            y=[y[i], y[i]],
            z=[zb, zt],
            mode='lines',
            line=dict(width=3),
            showlegend=False
        ))

    frames.append(go.Frame(
        data=[
            go.Surface(x=X, y=Y, z=Z, opacity=0.25,
                       colorscale='Greys', showscale=False),
            go.Scatter3d(x=x, y=y, z=[zt]*len(x),
                         mode='lines+markers'),
            go.Scatter3d(x=x, y=y, z=[zb]*len(x),
                         mode='lines+markers'),
            *frame_edges
        ]
    ))

fig.frames = frames
fig.show()